In [3]:
import os
import cv2
import numpy as np
import pandas as pd
import h5py
import tensorflow as tf
from tensorflow.keras.applications.resnet50 import ResNet50, preprocess_input
from tensorflow.keras.preprocessing import image
from tensorflow.keras.models import Model

## Face Recognition Function

In [2]:
# Load the pre-trained ResNet50 model
base_model = ResNet50(weights='imagenet', include_top=False)
model = Model(inputs=base_model.input, outputs=base_model.output)
# Modify pooling layer to global average pooling to get fixed size output. This results in a output vector of size 2048
x = base_model.output
x = tf.keras.layers.GlobalAveragePooling2D()(x)
model = Model(inputs=base_model.input, outputs=x)

# Load OpenCV's Haar Cascade for face detection
face_cascade = cv2.CascadeClassifier(cv2.data.haarcascades + 'haarcascade_frontalface_default.xml')

def extract_facial_features(frame):
    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    faces = face_cascade.detectMultiScale(gray, 1.3, 5)
    if len(faces) == 0:
        return None  # Return None if no faces are detected

    (x, y, w, h) = faces[0]  # Consider the first face
    face = frame[y:y+h, x:x+w]
    face = cv2.resize(face, (224, 224))
    face = cv2.cvtColor(face, cv2.COLOR_BGR2RGB)
    face = np.expand_dims(face, axis=0)
    face = preprocess_input(face)
    features = model.predict(face)

    return features.flatten()

In [1]:
# Load labels from CSV
labels_splits_df = pd.read_csv(r'../train_test_validate_split.csv')

# HDF5 file to save extracted features
h5_file = r'../facial_features.h5'

NameError: name 'pd' is not defined

In [4]:
videos_path = r'../CDS datasets/CMU-MOSEI/Raw'
frame_skip = 30

i_count = 1
with h5py.File(h5_file, 'w') as h5f:
    for index, row in labels_splits_df.iterrows():
        print(f'Processing {i_count} of {len(labels_splits_df)}')
        i_count += 1
        video_id = row['video_id']
        clip_id = row['clip_id']
        text = row['text']
        annotation = row['annotation']
        split = row['split']
        filename = f"{clip_id}.mp4"
        filepath = os.path.join(videos_path, str(video_id), filename)
        if not os.path.exists(filepath):
            continue  # Skip if the video file doesn't exist
        
        cap = cv2.VideoCapture(filepath)
        features_per_frame = []
        while cap.isOpened():
            ret, frame = cap.read()
            if not ret:
                break
            if cap.get(cv2.CAP_PROP_POS_FRAMES) % frame_skip == 0:
                features = extract_facial_features(frame)
                if features is not None:
                    features_per_frame.append(features)
        cap.release()

        if features_per_frame:
            # Calculate the average of the features
            average_features = np.mean(features_per_frame, axis=0)
            group_id = f'{video_id},{clip_id}'
            grp = h5f.create_group(group_id)
            grp.create_dataset('averaged_facial_features', data=average_features, compression="gzip")
            grp.attrs['label'] = annotation
            grp.attrs['text'] = text
            grp.attrs['split'] = split

Processing 1 of 14994
1/1 [==============================] - 0s 48ms/step
Processing 2 of 14994
1/1 [==============================] - 0s 48ms/step
Processing 3 of 14994
1/1 [==============================] - 0s 48ms/step
Processing 4 of 14994
1/1 [==============================] - 0s 47ms/step
Processing 5 of 14994
Processing 6 of 14994
1/1 [==============================] - 0s 48ms/step
Processing 7 of 14994
1/1 [==============================] - 0s 53ms/step
Processing 8 of 14994
1/1 [==============================] - 0s 47ms/step
Processing 9 of 14994
1/1 [==============================] - 0s 47ms/step
Processing 10 of 14994
1/1 [==============================] - 0s 47ms/step
Processing 11 of 14994
1/1 [==============================] - 0s 46ms/step
Processing 12 of 14994
1/1 [==============================] - 0s 51ms/step
Processing 13 of 14994
1/1 [==============================] - 0s 48ms/step
Processing 14 of 14994
1/1 [==============================] - 0s 77ms/step
Processing 